# import

In [1]:
import sys
import json
from anndata import AnnData
import cpa
import scanpy as sc
import importlib
import numpy as np
from tqdm import tqdm
import pickle
import os
import shutil
import torch

sys.path.append("/data1/lichen/code/single_cell_perturbation/scPerturb/Byte_Pert_Data/")
import v1
from v1.utils import *
from v1.dataloader import *

Global seed set to 0


In [2]:
importlib.reload(v1)
importlib.reload(v1.utils)
importlib.reload(v1.dataloader)

<module 'v1.dataloader' from '/data1/lichen/code/single_cell_perturbation/scPerturb/Byte_Pert_Data/v1/dataloader.py'>

# CPA跑unseen celltype

In [3]:
# =================================== initial

# - load common_pert
with open('/nfs/public/lichen/results/single_cell_perturbation/perturbation_benchmark/utils_data/prefix_gene_dict.json', 'r') as f:
    prefix_gene_dict = json.load(f)
with open('/nfs/public/lichen/results/single_cell_perturbation/perturbation_benchmark/utils_data/prefix_pert_dict.json', 'r') as f:
    prefix_pert_dict = json.load(f)
common_genes = np.intersect1d(prefix_gene_dict['ReplogleWeissman2022_K562_essential'],prefix_gene_dict['ReplogleWeissman2022_rpe1'])
common_perts = np.intersect1d(prefix_pert_dict['ReplogleWeissman2022_K562_essential'],prefix_pert_dict['ReplogleWeissman2022_rpe1'])
np.random.seed(2024)
np.random.shuffle(common_perts)

# - split the perts
split_point = int(len(common_perts) * 0.9)
test_perts = common_perts[:split_point]
val_perts = common_perts[split_point:]

# - init para
data_dir = '/nfs/public/lichen/data/single_cell/perturb_data/scPerturb/raw/scPerturb_rna/statistic_20240520'
pert_cell_filter = 100 # this is used to filter perts, cell number less than this will be filtered
seed = 2024 # this is the random seed
split_type = 1 # 1 for unseen perts; 0 for unseen celltypes
split_ratio = [0.7, 0.2, 0.1] # train:test:val; val is used to choose data, test is for final validation
var_num = 5000 # selecting hvg number
num_de_genes = 20 # number of de genes
bs_train = 32 # batch size of trainloader
bs_test = 32 # batch size of testloader
lr = 1e-4

def get_common_pert(pert_data, common_genes):
    # - get the common_genes **************
    pert_data.var_genes = list(common_genes)
    pert_data.adata_split = pert_data.adata_split[:, pert_data.var_genes].copy()
    pert_idx_dict = {}
    for pert, tmp_list in pert_data.adata_split.uns['rank_genes_groups'].items():
        idx_list = []
        for i, gene in enumerate(tmp_list):
            if gene in pert_data.adata_split.var_names:
                idx_list.append(i)
        pert_idx_dict[pert] = idx_list
    for key in pert_data.adata_split.uns.keys():
        print(key)
        ele = pert_data.adata_split.uns[key]
        for pert in ele.keys():
            ele[pert] = list(np.array(ele[pert])[pert_idx_dict[pert]])

tmp_dir = '/nfs/public/lichen/results/single_cell_perturbation/perturbation_benchmark/scPerturb'
# - load k562 pert_data
prefix = 'ReplogleWeissman2022_K562_essential'
save_prefix = f'GEARS_v2-prefix_{prefix}-pert_cell_filter_{pert_cell_filter}-\
seed_{seed}-split_type_{split_type}-var_num_{var_num}-num_de_genes_{num_de_genes}-bs_train_{bs_train}-\
bs_test_{bs_test}'
save_dir = os.path.join(tmp_dir, prefix, save_prefix)
pert_data_1 = pickle.load(open(os.path.join(save_dir,'pert_data.pkl'), 'rb'))
get_common_pert(pert_data_1, common_genes)
print('='*20, 'k562 pert_data loaded')

# - load rpe1 pert_data
prefix = 'ReplogleWeissman2022_rpe1'
save_prefix = f'GEARS_v2-prefix_{prefix}-pert_cell_filter_{pert_cell_filter}-\
seed_{seed}-split_type_{split_type}-var_num_{var_num}-num_de_genes_{num_de_genes}-bs_train_{bs_train}-\
bs_test_{bs_test}'
save_dir = os.path.join(tmp_dir, prefix, save_prefix)
pert_data_2 = pickle.load(open(os.path.join(save_dir,'pert_data.pkl'), 'rb'))
get_common_pert(pert_data_2, common_genes)
print('='*20, 'rpe1 pert_data loaded')

# - modify 2 pert_data
pert_data_1.modify_gears(without_subgroup=True)
pert_data_2.modify_gears(without_subgroup=True)

# - give celltypes
cell_type_1, cell_type_2 = 'K562', 'retinal pigment epithelial cells'

# - get pert_gorups
pert_groups_1 = [i+' | '+cell_type_1 for i in common_perts]
pert_groups_2 = [i+' | '+cell_type_2 for i in common_perts]

adata_1 = pert_data_1.adata_split.copy()
adata_2 = pert_data_2.adata_split.copy()

rank_genes_groups
pvals
pvals_adj
scores
logfoldchanges
==================== k562 pert_data loaded
rank_genes_groups
pvals
pvals_adj
scores
logfoldchanges
==================== rpe1 pert_data loaded
add adata finished
add condition finished
add set2conditions finished
add adata finished
add condition finished
add set2conditions finished


In [4]:
# - model initial
model_params = {
    "n_latent": 64,
    "recon_loss": "nb",
    "doser_type": "linear",
    "n_hidden_encoder": 128,
    "n_layers_encoder": 2,
    "n_hidden_decoder": 512,
    "n_layers_decoder": 2,
    "use_batch_norm_encoder": True,
    "use_layer_norm_encoder": False,
    "use_batch_norm_decoder": False,
    "use_layer_norm_decoder": True,
    "dropout_rate_encoder": 0.0,
    "dropout_rate_decoder": 0.1,
    "variational": False,
    "seed": 6977,
}

trainer_params = {
    "n_epochs_kl_warmup": None,
    "n_epochs_pretrain_ae": 30,
    "n_epochs_adv_warmup": 50,
    "n_epochs_mixup_warmup": 0,
    "mixup_alpha": 0.0,
    "adv_steps": None,
    "n_hidden_adv": 64,
    "n_layers_adv": 3,
    "use_batch_norm_adv": True,
    "use_layer_norm_adv": False,
    "dropout_rate_adv": 0.3,
    "reg_adv": 20.0,
    "pen_adv": 5.0,
    "lr": 0.0003,
    "wd": 4e-07,
    "adv_lr": 0.0003,
    "adv_wd": 4e-07,
    "adv_loss": "cce",
    "doser_lr": 0.0003,
    "doser_wd": 4e-07,
    "do_clip_grad": True,
    "gradient_clip_value": 1.0,
    "step_size_lr": 10,
}

In [5]:


pert_cat_list, pred_list, truth_list, pred_de_list, truth_de_list = [], [], [], [], []
for i in tqdm(range(len(pert_groups_1))):
    # i = 133
    fix_seed(2024)
    #  - get adatas
    pert_group_1, pert_group_2 = pert_groups_1[i], pert_groups_2[i]
    
    adata_pert_1 = adata_1[adata_1.obs['perturbation_group']==pert_group_1]
    adata_pert_2 = adata_2[adata_2.obs['perturbation_group']==pert_group_2]
    
    adata_ctrl_1 = adata_1[adata_pert_1.obs['control_barcode']]
    adata_ctrl_2 = adata_2[adata_pert_2.obs['control_barcode']]
    
    # - generate adata_train to input to scGen model
    np_list, obs_list, pert_list, celltype_list = [], [], [], []
    pert_list_2 = []
    adata_list = [adata_pert_1, adata_pert_2, adata_ctrl_1, adata_ctrl_2]
    for j, adata_ in enumerate(adata_list):
        if j == 0 or j == 1:
            pert_list_2.extend([pert_group_1.split(' | ')[0]]*len(adata_))
            pert_list.extend(['stimulated']*len(adata_))
        else:
            pert_list_2.extend(['ctrl']*len(adata_))
            pert_list.extend(['ctrl']*len(adata_))
        celltype_list.extend([adata_.obs['celltype_new'][0]]*len(adata_))
        obs_list.extend([obs+f'_{j}' for obs in adata_.obs_names])
        np_list.append(adata_.X.toarray())

    adata_train = AnnData(X = np.vstack(np_list))
    adata_train.obs_names = obs_list
    adata_train.var_names = adata_pert_1.var_names

    adata_train.obs['condition'] = pert_list
    adata_train.obs['condition_2'] = pert_list_2
    adata_train.obs['cell_type'] = celltype_list
    
    # - transform the adata_train.X to count
    adata_train.obs['cov_cond'] = adata_train.obs['cell_type'] + '_' + adata_train.obs['condition']
    adata_train.X = np.exp(adata_train.X)-1
    
    # - initial model
    cpa.CPA.setup_anndata(adata_train, 
                        perturbation_key='condition',
                        control_group='ctrl',
                        #   dosage_key='dose',
                        categorical_covariate_keys=['cell_type'],
                        is_count_data=True,
                        #   deg_uns_key='rank_genes_groups_cov',
                        deg_uns_cat_key='cov_cond',
                        max_comb_len=1,
                        )

    # - set the train and validation for cpa
    # -- get total obs_names of the pert
    adata_train_new = adata_train[~((adata_train.obs["cell_type"] == cell_type_2) &
                        (adata_train.obs["condition"] == "stimulated"))].copy()

    # obs_df_split = adata_train_new.obs
    obs_df_sub_idx = np.array(adata_train_new.obs.index)

    np.random.seed(2024)
    np.random.shuffle(obs_df_sub_idx)

    # -- data split
    split_point_1 = int(len(obs_df_sub_idx) * 0.9)
    split_point_2 = int(len(obs_df_sub_idx) * (0.9+0.1))
    train = obs_df_sub_idx[:split_point_1]
    valid = obs_df_sub_idx[split_point_1:split_point_2]


    adata_train.obs['split_key'] = 'ood'

    # -- set the test row
    adata_train.obs.loc[train,'split_key'] = 'train'
    adata_train.obs.loc[valid,'split_key'] = 'valid'

    # - initial the model and training   
    model = cpa.CPA(adata=adata_train, 
                    split_key='split_key',
                    train_split='train',
                    valid_split='valid',
                    test_split='ood',
                    **model_params,
                )

    model.train(max_epochs=2000,
                use_gpu=True, 
                batch_size=500,
                plan_kwargs=trainer_params,
                early_stopping_patience=5,
                check_val_every_n_epoch=5,
                # save_path='../../datasets/',
                progress_bar_refresh_rate = 0
            )

    # - predict result
    model.predict(adata_train, batch_size=2048)

    # - get the pred data
    cat = cell_type_2 + '_' + 'stimulated'
    cat_adata = adata_train[adata_train.obs['cov_cond'] == cat].copy()
    x_pred = cat_adata.obsm['CPA_pred']
    x_pred = np.log1p(x_pred)

    # ====================================== generate out.pkl
    # - get test_res
    pert_gears = transform_name(pert_group_2)
    geneid2idx = dict(zip(pert_data_2.adata.var.index.values, range(len(pert_data_2.adata.var.index.values))))
    pert2pert_full_id = dict(pert_data_2.adata.obs[['condition', 'condition_name']].values)
    de_idx = [geneid2idx[j] for j in pert_data_2.adata.uns['rank_genes_groups_cov_all'][pert2pert_full_id[pert_gears]][:20]]

    # - add to list
    pert_cat_list.append(np.array([pert_gears]*adata_pert_2.shape[0]))
    pred_list.append(x_pred)
    truth_list.append(adata_pert_2.X.toarray())
    pred_de_list.append(x_pred[:,de_idx])
    truth_de_list.append(adata_pert_2.X.toarray()[:, de_idx])
    
    torch.cuda.empty_cache()
    del model
    
    # break

  0%|          | 0/490 [00:00<?, ?it/s]

100%|██████████| 546/546 [00:00<00:00, 416455.72it/s]
An NVIDIA GPU may be present on this machine, but a CUDA-enabled jaxlib is not installed. Falling back to cpu.


INFO     Generating sequential column names                                                                        
INFO     Generating sequential column names                                                                        


Global seed set to 6977
100%|██████████| 2/2 [00:00<00:00, 481.80it/s]
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
You are using a CUDA device ('NVIDIA GeForce RTX 3090') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]

Epoch 00004: cpa_metric reached. Module best state updated.

Epoch 00009: cpa_metric reached. Module best state updated.



disnt_basal = 1.2173913043478262
disnt_after = 1.2347826086956522
val_r2_mean = 0.042134722073872886
val_r2_var = -2.0711426734924316


...


Epoch 00024: cpa_metric reached. Module best state updated.

Epoch 00029: cpa_metric reached. Module best state updated.



disnt_basal = 1.319326075909225
disnt_after = 1.7999999999999998
val_r2_mean = 0.943767766157786
val_r2_var = -2.6144959131876626



Epoch 00034: cpa_metric reached. Module best state updated.

Epoch 00039: cpa_metric reached. Module best state updated.



disnt_basal = 1.2248703892157589
disnt_after = 1.7999999999999998
val_r2_mean = 0.9380850593249003
val_r2_var = -2.5598665873209634

disnt_basal = 1.4005554190889486
disnt_after = 1.7999999999999998
val_r2_mean = 0.9336636066436768
val_r2_var = -2.4872336387634277

disnt_basal = 1.401630775949125
disnt_after = 1.7999999999999998
val_r2_mean = 0.9372077385584513
val_r2_var = -2.415231784184774


100%|██████████| 490/490 [1:57:01<00:00, 14.33s/it]


In [6]:
test_res = {}
test_res['pert_cat'] = np.hstack(pert_cat_list)
test_res['pred'] = np.vstack(pred_list)
test_res['truth'] = np.vstack(truth_list)
test_res['pred_de'] = np.vstack(pred_de_list)
test_res['truth_de'] = np.vstack(truth_de_list)
# - get the out
out = get_metric(pert_data_2.adata, test_res)
# out_non_dropout = non_dropout_analysis(pert_data_2.adata, test_res)

tmp_dir = '/nfs/public/lichen/results/single_cell_perturbation/perturbation_benchmark_202410/unseen_celltype/K562_RPE1/result'
prefix = 'CPA_v1'
save_dir = os.path.join(tmp_dir, prefix)
os.makedirs(save_dir, exist_ok=True)
pickle.dump(out, open(os.path.join(save_dir,f'out.pkl'), 'wb'))
pickle.dump(test_res, open(os.path.join(save_dir,f'test_res.pkl'), 'wb'))
# pickle.dump(out_non_dropout, open(os.path.join(save_dir,f'out_non_dropout.pkl'), 'wb'))

get metrics... ...


100%|██████████| 490/490 [01:44<00:00,  4.69it/s]
